# Imports and definitions

In [1]:
import itertools
import pathlib
import shutil
import sys
import time

import pandas
import plotly
import plotly.express
import plotly.graph_objects
import plotly.subplots
import plotly.express.colors

In [2]:
image_classifier_cifar10_resnet18_layer_order = [
    
    "adapter.backbone.conv1",
    "adapter.backbone.bn1",
    "adapter.backbone.relu",
    "adapter.backbone.maxpool",
    
    "adapter.backbone.layer1.0.conv1",
    "adapter.backbone.layer1.0.bn1",
    "adapter.backbone.layer1.0.relu",
    "adapter.backbone.layer1.0.conv2",
    "adapter.backbone.layer1.0.bn2",
    
    "adapter.backbone.layer1.1.conv1",
    "adapter.backbone.layer1.1.bn1",
    "adapter.backbone.layer1.1.relu",
    "adapter.backbone.layer1.1.conv2",
    "adapter.backbone.layer1.1.bn2",
    
    "adapter.backbone.layer2.0.conv1",
    "adapter.backbone.layer2.0.bn1",
    "adapter.backbone.layer2.0.relu",
    "adapter.backbone.layer2.0.conv2",
    "adapter.backbone.layer2.0.bn2",
    "adapter.backbone.layer2.0.downsample.0",
    "adapter.backbone.layer2.0.downsample.1",
    
    "adapter.backbone.layer2.1.conv1",
    "adapter.backbone.layer2.1.bn1",
    "adapter.backbone.layer2.1.relu",
    "adapter.backbone.layer2.1.conv2",
    "adapter.backbone.layer2.1.bn2",
    
    "adapter.backbone.layer3.0.conv1",
    "adapter.backbone.layer3.0.bn1",
    "adapter.backbone.layer3.0.relu",
    "adapter.backbone.layer3.0.conv2",
    "adapter.backbone.layer3.0.bn2",
    "adapter.backbone.layer3.0.downsample.0",
    "adapter.backbone.layer3.0.downsample.1",
    
    "adapter.backbone.layer3.1.conv1",
    "adapter.backbone.layer3.1.bn1",
    "adapter.backbone.layer3.1.relu",
    "adapter.backbone.layer3.1.conv2",
    "adapter.backbone.layer3.1.bn2",
    
    "adapter.backbone.layer4.0.conv1",
    "adapter.backbone.layer4.0.bn1",
    "adapter.backbone.layer4.0.relu",
    "adapter.backbone.layer4.0.conv2",
    "adapter.backbone.layer4.0.bn2",
    "adapter.backbone.layer4.0.downsample.0",
    "adapter.backbone.layer4.0.downsample.1",
    
    "adapter.backbone.layer4.1.conv1",
    "adapter.backbone.layer4.1.bn1",
    "adapter.backbone.layer4.1.relu",
    "adapter.backbone.layer4.1.conv2",
    "adapter.backbone.layer4.1.bn2",
    
    "adapter.backbone.avgpool",
    
    "adapter.head",
]

image_classifier_cifar10_vgg11_layer_order = [f"adapter.backbone.{x}" for x in range(0, 21)] + ["adapter.head"]

# to be used for sorting dataframe layer names
def sorting(reference):
    def key(series):
        unsorted = list(series)
        return pandas.Series([reference.index(el) for el in unsorted])
    return key

experiment_name_conversion_dict = {
    # for random_neuron_bit_weighting in fault aware training
    "False_random": "RBIN",
    "True_random": "RBRN",
    "False_linear": "LBIN",
    "True_linear": "LBRN",
    "False_exponential": "EBIN",
    "True_exponential": "EBRN",
    "False_gradient": "GBIN",
    "True_gradient": "GBRN",
    # for random_neuron_bit_weighting_injection_type in fault aware training
    "False_random_None": "RBIN",
    "True_random_None": "RBRN",
    "False_linear_None": "LBIN",
    "True_linear_None": "LBRN",
    "False_exponential_None": "EBIN",
    "True_exponential_None": "EBRN",
    "False_gradient_None": "GBIN",
    "True_gradient_None": "GBRN",
    "False_random_activation": "RBINo",
    "True_random_activation": "RBRNo",
    "False_linear_activation": "LBINo",
    "True_linear_activation": "LBRNo",
    "False_exponential_activation": "EBINo",
    "True_exponential_activation": "EBRNo",
    "False_gradient_activation": "GBINo",
    "True_gradient_activation": "GBRNo",
    "False_random_weight": "RBINw",
    "True_random_weight": "RBRNw",
    "False_linear_weight": "LBINw",
    "True_linear_weight": "LBRNw",
    "False_exponential_weight": "EBINw",
    "True_exponential_weight": "EBRNw",
    "False_gradient_weight": "GBINw",
    "True_gradient_weight": "GBRNw",
}

configuration_name_to_nice_name_mapping = {
    "resnet18_gtsrb": "ResNet18<br>GTSRB",
    "resnet18_cifar10": "ResNet18<br>CIFAR10",
    "vgg11_gtsrb": "VGG11<br>GTSRB",
    "vgg11_cifar10": "VGG11<br>CIFAR10",
}
configuration_order = list(configuration_name_to_nice_name_mapping.keys())

experiment_sorting_list = [
    "GBINo", "GBRNo",
    "EBINo", "EBRNo",
    "LBINo", "LBRNo",
    "RBINo", "RBRNo",
    "GBINw", "GBRNw",
    "EBINw", "EBRNw",
    "LBINw", "LBRNw",
    "RBINw", "RBRNw",
]

# max_float = sys.float_info.max
max_float = 2.0e34

# alltogether_experiments_to_plot = ["EBINo", "RBRNo", "EBINw", "RBRNw"]
alltogether_experiments_to_plot = experiment_sorting_list
histogram_line_injection_target = "weight"
if histogram_line_injection_target == "activation":
    histogram_line_experiments = [
        "GBINo", "GBRNo",
        "EBINo", "EBRNo",
        "LBINo", "LBRNo",
        "RBINo", "RBRNo",
    ]
elif histogram_line_injection_target == "weight":
    histogram_line_experiments = [
        "GBINw", "GBRNw",
        "EBINw", "EBRNw",
        "LBINw", "LBRNw",
        "RBINw", "RBRNw",
    ]
else:
    raise ValueError()
histogram_experiment_full_ids_to_plot = [x + "_resnet18_cifar10" for x in histogram_line_experiments]
line_experiment_full_ids_to_plot = histogram_experiment_full_ids_to_plot

metric_names = ["accuracy", "cross_entropy"]

sdc_thresholds = {
    metric_names[0]: list(map(lambda x: x / 100, range(-5, 105, 5))),
    metric_names[1]: list(map(lambda x: 10 ** x, range(-1, 11))),
}
metric_classification_functions = {
    metric_names[0]: {
        "true_positive": lambda baseline, series, threshold: (baseline - series) / baseline >= threshold,
        "false_positive": lambda baseline, series, threshold: (baseline - series) / baseline < threshold,
    },
    metric_names[1]: {
        "true_positive": lambda baseline, series, threshold: (series / baseline) >= threshold,
        "false_positive": lambda baseline, series, threshold: (series / baseline) < threshold,
    },
}

metric_names = metric_names[:1]
sdc_thresholds = {
#     metric_names[0]: [0.05, 0.25, 0.5],
    metric_names[0]: [0.05],
}




TIME_FORMAT = "%Y_%m_%d__%H_%M_%S_%z"

# Data Import

## Path Definitions

In [3]:
# base path for IJCNN2023
base_ijcnn2023_result_path = pathlib.Path().cwd() / "../scripts/results/sparse_results_ijcnn2023/"

# # we assume we are in the enpheeph/notebooks folder
# result_paths = {
#     # IJCNN2023, seed 1600, 24-hour time limit (reached before 10e6 injections) is common
#     # comparison between the different algorithms, done on resnet18 gtsrb, weight injection
#     # exponential bit importance neuron
#     "EBIN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "importance_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_11__00_13_06_+0100/",
#     ],
#     # random bit random neuron
#     "RBRN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "random_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_1.0__2023_01_11__00_13_46_+0100/",
#     ],
#     # random bit importance neuron
#     "RBIN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0__2023_01_15__16_52_25_+0100/",
#     ],
#     # exponential bit random neuron
#     "EBRN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "importance-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_1.0__2023_01_12__20_21_45_+0100/",
#     ], 
#     # gradient bit importance neuron
#     "GBIN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_sparse_target_None__2023_01_16__01_44_54_+0100/",
#     ],
#     # gradient bit random neuron
#     "GBRN_resnet18_gtsrb_weight": [
#         base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_sparse_target_None__2023_01_16__01_43_27_+0100/",
#     ],
# }
# we assume we are in the enpheeph/notebooks folder
# result_paths = {
#     # IJCNN2023, seed 1600, 24-hour time limit (reached before 10e6 injections) is common
#     # comparison between the different algorithms, done on resnet18 gtsrb, activation injection
#     # exponential bit importance neuron
#     "EBIN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "importance_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_0.0__2023_01_04__01_01_25_+0100/",
#     ],
#     # random bit random neuron
#     "RBRN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "random_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_3_starting_seed_1600_random_threshold_1.0__2023_01_05__13_33_35_+0100/",
#     ],
#     # random bit importance neuron
#     "RBIN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_random_sparse_target_None__2023_01_18__12_16_36_+0100/",
#     ],
#     # exponential bit random neuron
#     "EBRN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "exponential-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_exponential_sparse_target_None__2023_01_18__12_20_00_+0100/",
#     ],
#     # gradient bit importance neuron
#     "GBIN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1,2_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_approximate_activation_gradient_value_True_sparse_target_None__2023_01_22__17_41_47_+0100/",
#     ],
#     # gradient bit random neuron
#     "GBRN_resnet18_gtsrb_activation": [
#         base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1,2_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_approximate_activation_gradient_value_True_sparse_target_None__2023_01_22__17_38_49_+0100/",
#     ],
# }
# all the results we have
result_paths = {
    # IJCNN2023, seed 1600, 24-hour time limit (reached before 10e6 injections) is common
    # comparison across all experiments
    
    # resnet18 gtsrb activation
    # exponential bit importance neuron
    "EBINo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "importance_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_0.0__2023_01_04__01_01_25_+0100/",
    ],
    # random bit random neuron
    "RBRNo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "random_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_3_starting_seed_1600_random_threshold_1.0__2023_01_05__13_33_35_+0100/",
    ],
    # random bit importance neuron
    "RBINo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_random_sparse_target_None__2023_01_18__12_16_36_+0100/",
    ],
    # exponential bit random neuron
    "EBRNo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "exponential-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_exponential_sparse_target_None__2023_01_18__12_20_00_+0100/",
    ],
    # gradient bit importance neuron
    "GBINo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1,2_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_approximate_activation_gradient_value_True_sparse_target_None__2023_01_22__17_41_47_+0100/",
    ],
    # gradient bit random neuron
    "GBRNo_resnet18_gtsrb_activation": [
        base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_activation_devices_1,2_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_approximate_activation_gradient_value_True_sparse_target_None__2023_01_22__17_38_49_+0100/",
    ],
    
    # resnet18 gtsrb weight
    # exponential bit importance neuron
    "EBINw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "importance_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_11__00_13_06_+0100/",
    ],
    # random bit random neuron
    "RBRNw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "random_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_1.0__2023_01_11__00_13_46_+0100/",
    ],
    # random bit importance neuron
    "RBINw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0__2023_01_15__16_52_25_+0100/",
    ],
    # exponential bit random neuron
    "EBRNw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "importance-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_1.0__2023_01_12__20_21_45_+0100/",
    ], 
    # gradient bit importance neuron
    "GBINw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_sparse_target_None__2023_01_16__01_44_54_+0100/",
    ],
    # gradient bit random neuron
    "GBRNw_resnet18_gtsrb_weight": [
        base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/resnet18_gtsrb/epoch-29-step19980_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_sparse_target_None__2023_01_16__01_43_27_+0100/",
    ],
    
    # resnet18 cifar10 activation
    # random bit random neuron
    "RBRNo_resnet18_cifar10_activation": [
        base_ijcnn2023_result_path / "random_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_1.0__2023_01_06__15_49_29_+0100/",
    ],
    # exponential bit importance neuron
    "EBINo_resnet18_cifar10_activation": [
        base_ijcnn2023_result_path / "importance_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_activation_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_06__15_48_45_+0100/",
    ],
    
    # resnet18 cifar10 weight
    # random bit random neuron
    "RBRNw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "random_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_1.0__2023_01_12__00_31_04_+0100/",
    ],
    # random bit importance neuron
    "RBINw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_15__16_51_26_+0100/",
    ],
    # exponential bit importance neuron
    "EBINw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "importance_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_12__00_30_35_+0100/",
    ],
    # exponential bit random neuron
    "EBRNw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "importance-bit-random-neuron_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_exponential_sparse_target_None__2023_01_16__18_00_01_+0100/",
    ],
    # gradient bit random neuron
    "GBRNw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_sparse_target_None__2023_01_17__02_14_28_+0100/",
    ],
    # gradient bit importance neuron
    "GBINw_resnet18_cifar10_weight": [
        base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/resnet18_cifar10/epoch-30-step38750_0_pruning/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_sparse_target_None__2023_01_16__01_44_39_+0100/",
    ],
    
    # vgg11 gtsrb activation
    # random bit random neuron
    "RBRNo_vgg11_gtsrb_activation": [
        base_ijcnn2023_result_path / "random_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_activation_devices_2_starting_seed_1600_random_threshold_1.0__2023_01_07__17_46_03_+0100/",
    ],
    # exponential bit importance neuron
    "EBINo_vgg11_gtsrb_activation": [
        base_ijcnn2023_result_path / "importance_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_activation_devices_3_starting_seed_1600_random_threshold_0.0__2023_01_07__17_45_43_+0100/",
    ],
    
    # vgg11 gtsrb weight
    # random bit random neuron
    "RBRNw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "random_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0__2023_01_13__01_07_14_+0100/",
    ],
    # random bit importance neuron
    "RBINw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_random_sparse_target_None__2023_01_16__18_00_46_+0100/",
    ],
    # exponential bit importance neuron
    "EBINw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "importance_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_0.0__2023_01_13__01_07_24_+0100/",
    ],
    # exponential bit random neuron
    "EBRNw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "importance-bit-random-neuron_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_1.0_bit_weighting_exponential_sparse_target_None__2023_01_16__22_57_28_+0100/",
    ],
    # gradient bit random neuron
    "GBRNw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_sparse_target_None__2023_01_18__11_26_33_+0100/",
    ],
    # gradient bit importance neuron
    "GBINw_vgg11_gtsrb_weight": [
        base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/vgg11_gtsrb/epoch-29-step19980/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_sparse_target_None__2023_01_17__02_15_45_+0100/",
    ],
    
    # vgg11 cifar10 activation
    # random bit random neuron
    "RBRNo_vgg11_cifar10_activation": [
        base_ijcnn2023_result_path / "random_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_activation_devices_1_starting_seed_1600_random_threshold_1.0__2023_01_09__19_47_52_+0100/",
    ],
    # exponential bit importance neuron
    "EBINo_vgg11_cifar10_activation": [
        base_ijcnn2023_result_path / "importance_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_activation_devices_3_starting_seed_1600_random_threshold_0.0__2023_01_08__19_32_51_+0100/",
    ],
    
    # vgg11 cifar10 weight
    # random bit random neuron
    "RBRNw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "random_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_1.0__2023_01_14__02_52_18_+0100/",
    ],
    # random bit importance neuron
    "RBINw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "random-bit-importance-neuron_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_3_starting_seed_1600_random_threshold_0.0_bit_weighting_random_sparse_target_None__2023_01_16__22_58_16_+0100/",
    ],
    # exponential bit importance neuron
    "EBINw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "importance_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0__2023_01_14__02_51_57_+0100/",
    ],
    # exponential bit random neuron
    "EBRNw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "importance-bit-random-neuron_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_1.0_bit_weighting_exponential_sparse_target_None__2023_01_18__11_23_38_+0100/",
    ],
    # gradient bit random neuron
    "GBRNw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "gradient-bit-random-neuron_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_2_starting_seed_1600_random_threshold_1.0_bit_weighting_gradient_sparse_target_None__2023_01_18__11_26_44_+0100/",
    ],
    # gradient bit importance neuron
    "GBINw_vgg11_cifar10_weight": [
        base_ijcnn2023_result_path / "gradient-bit-importance-neuron_sampling/vgg11_cifar10/epoch-4-step6250/results_injection_type_weight_devices_1_starting_seed_1600_random_threshold_0.0_bit_weighting_gradient_sparse_target_None__2023_01_17__02_14_42_+0100/",
    ],
    
# }
# result_paths = {
    "alltogether": [
        base_ijcnn2023_result_path / "alltogether",
    ],
}
# we want to compare all the resnet18 gtsrb weight with the different values of random-importance
# result_path = result_paths["importance_vgg11_cifar10_activation"]

## CSV Parsing

In [4]:
csv_list = {}
for name, paths in result_paths.items():
    original_csvs = []
    csv = pandas.DataFrame()
    for path in paths:
        for csv_file in path.glob("**/*.csv"):
            new_csv_file = csv_file.with_suffix(".csv.new")
            shutil.copy(csv_file, new_csv_file)
            text = new_csv_file.read_text()
            text = text.replace(".ckpt2", ".ckpt,2")
            new_csv_file.write_text(text)
            new_csv = pandas.read_csv(
                new_csv_file,
                sep=",",
                header=0,
                index_col=0,
                # dtype=str,
                engine="python",
                # nrows=3400,
                on_bad_lines="warn",
            )
            if not len(new_csv):
                continue
            for metric in metric_names:
                new_csv[f"test_{metric}_baseline"] = new_csv.loc[0, f"test_{metric}_baseline"].tolist()
            csv = pandas.concat(
                [
                    csv,
                    new_csv.reset_index()
                ],
                axis=0,
            )
            original_csvs.append(new_csv.copy())
    csv_list[name] = {"csv": csv.reset_index(drop=True), "original_csvs": original_csvs}

## Data Processing

In [5]:
# to add experiment name and configuration name to everyone, even the common executions
# putting everything in a single csv as well
csv = pandas.DataFrame()
for name, c in csv_list.copy().items():
    c = c["csv"]
    if "experiment_code" not in c.columns:
        c["experiment_code"] = [name.split("_")[0]] * len(c.index)
    if "config_file" not in c.columns:
        c["experiment_config"] = ["_".join(name.split("_")[1:3])] * len(c.index)
    else:
        experiment_configs = []
        for e in c["config_file"]:
            experiment_configs.append([n for n in configuration_name_to_nice_name_mapping.keys() if n in e][0])
        c["experiment_config"] = experiment_configs
    experiment_full_id = []
    experiment_full_id_seed = []
    for experiment_code, experiment_config, seed in zip(list(c["experiment_code"]), list(c["experiment_config"]), list(c["random_seed"])):
        experiment_full_id.append("_".join([experiment_code, experiment_config,]))
        experiment_full_id_seed.append("_".join([experiment_code, experiment_config, str(seed)]))
    c["experiment_full_id"] = experiment_full_id
    c["experiment_full_id_seed"] = experiment_full_id_seed
    csv = pandas.concat(
        [
            csv,
            c.reset_index()
        ],
        axis=0,
    )
csv.head()

level_0  i  random_seed  random_threshold                        timestamp  \
0        0  0         1600               0.0  2023-01-04T00:02:00.000018+0000   
1        1  1         1600               0.0  2023-01-04T00:02:12.197240+0000   
2        2  2         1600               0.0  2023-01-04T00:02:25.163125+0000   
3        3  3         1600               0.0  2023-01-04T00:02:30.733914+0000   
4        4  4         1600               0.0  2023-01-04T00:02:39.142023+0000   

                                          target_csv injection_type  \
0  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
1  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
2  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
3  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
4  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   

  extra_injection_info                       layer_name    index  ...  \
0                  NaN           adapter.backbone.conv1  30-7-17  ...   
1                  NaN   adapter.backbone.layer4.0.relu  195-1-0  ...   
2                  NaN   adapter.backbone.layer2.1.relu   68-3-3  ...   
3                  NaN  adapter.backbone.layer2.0.conv2    4-4-2  ...   
4                  NaN                     adapter.head        9  ...   

   test_cross_entropy_injected experiment_code  experiment_config  \
0                 2.783694e+19           EBINo     resnet18_gtsrb   
1                 2.097106e-01           EBINo     resnet18_gtsrb   
2                 3.735838e+07           EBINo     resnet18_gtsrb   
3                          NaN           EBINo     resnet18_gtsrb   
4                          NaN           EBINo     resnet18_gtsrb   

     experiment_full_id    experiment_full_id_seed  bit_weighting  \
0  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
1  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
2  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
3  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
4  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   

  random_neuron approximate_activation_gradient_value config_file  \
0           NaN                                   NaN         NaN   
1           NaN                                   NaN         NaN   
2           NaN                                   NaN         NaN   
3           NaN                                   NaN         NaN   
4           NaN                                   NaN         NaN   

  checkpoint_file  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  

[5 rows x 25 columns]

In [6]:
# remove NaN and inf values
# csv.sort_values("test_cross_entropy_injected", ascending=False)
for experiment_full_id in pandas.unique(csv["experiment_full_id"]):
    filter_flag = csv["experiment_full_id"] == experiment_full_id
    for metric_name in metric_names:
        csv.loc[filter_flag, f"test_{metric_name}_injected"] = csv.loc[filter_flag, f"test_{metric_name}_injected"].replace(float("inf"), max_float)
        csv.loc[filter_flag, f"test_{metric_name}_injected"] = csv.loc[filter_flag, f"test_{metric_name}_injected"].replace(float("-inf"), -max_float)
    csv.loc[filter_flag, "test_accuracy_injected"] = csv.loc[filter_flag, "test_accuracy_injected"].replace(float("NaN"), 0.0)
    csv.loc[filter_flag, "test_cross_entropy_injected"] = csv.loc[filter_flag, "test_cross_entropy_injected"].replace(float("NaN"), max_float)
csv.head()

level_0  i  random_seed  random_threshold                        timestamp  \
0        0  0         1600               0.0  2023-01-04T00:02:00.000018+0000   
1        1  1         1600               0.0  2023-01-04T00:02:12.197240+0000   
2        2  2         1600               0.0  2023-01-04T00:02:25.163125+0000   
3        3  3         1600               0.0  2023-01-04T00:02:30.733914+0000   
4        4  4         1600               0.0  2023-01-04T00:02:39.142023+0000   

                                          target_csv injection_type  \
0  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
1  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
2  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
3  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
4  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   

  extra_injection_info                       layer_name    index  ...  \
0                  NaN           adapter.backbone.conv1  30-7-17  ...   
1                  NaN   adapter.backbone.layer4.0.relu  195-1-0  ...   
2                  NaN   adapter.backbone.layer2.1.relu   68-3-3  ...   
3                  NaN  adapter.backbone.layer2.0.conv2    4-4-2  ...   
4                  NaN                     adapter.head        9  ...   

   test_cross_entropy_injected experiment_code  experiment_config  \
0                 2.783694e+19           EBINo     resnet18_gtsrb   
1                 2.097106e-01           EBINo     resnet18_gtsrb   
2                 3.735838e+07           EBINo     resnet18_gtsrb   
3                 2.000000e+34           EBINo     resnet18_gtsrb   
4                 2.000000e+34           EBINo     resnet18_gtsrb   

     experiment_full_id    experiment_full_id_seed  bit_weighting  \
0  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
1  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
2  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
3  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   
4  EBINo_resnet18_gtsrb  EBINo_resnet18_gtsrb_1600            NaN   

  random_neuron approximate_activation_gradient_value config_file  \
0           NaN                                   NaN         NaN   
1           NaN                                   NaN         NaN   
2           NaN                                   NaN         NaN   
3           NaN                                   NaN         NaN   
4           NaN                                   NaN         NaN   

  checkpoint_file  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  

[5 rows x 25 columns]

In [7]:
# we want to compute the precision and the recall of the injection
# we need to add columns for labelling each injection as true positive or false positive, based on the
# SDC/DUE threshold

# we assume all the faults can be categorized as positive, either true if accuracy drop is bigger than threshold
# or false if below

for experiment_full_id in pandas.unique(csv["experiment_full_id"]):
    filter_flag = csv["experiment_full_id"] == experiment_full_id
    for metric_name in metric_names:
        baseline = pandas.unique(csv.loc[filter_flag, f"test_{metric_name}_baseline"])[0]
        for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]):
            true_positive = metric_classification_functions[metric_name]["true_positive"](baseline, csv.loc[filter_flag, f"test_{metric_name}_injected"], sdc_threshold)
            false_positive = metric_classification_functions[metric_name]["false_positive"](baseline, csv.loc[filter_flag, f"test_{metric_name}_injected"], sdc_threshold)
            precision = pandas.Series([true_positive[:i+1].sum() / (true_positive[:i+1].sum() + false_positive[:i+1].sum()) for i in range(len(true_positive))])
            print(experiment_full_id, metric_name, sdc_threshold, precision.tolist()[-1])
            csv.loc[filter_flag, f"SDC_{metric_name}_{sdc_threshold}_precision"] = precision.tolist()
            csv.loc[filter_flag, f"SDC_{metric_name}_{sdc_threshold}_true_positive"] = true_positive.tolist()
            csv.loc[filter_flag, f"SDC_{metric_name}_{sdc_threshold}_false_positive"] = false_positive.tolist()
            for experiment_full_id_seed in pandas.unique(csv.loc[filter_flag, "experiment_full_id_seed"]):
                filter_flag_seed = csv["experiment_full_id_seed"] == experiment_full_id_seed
                true_positive = metric_classification_functions[metric_name]["true_positive"](baseline, csv.loc[filter_flag_seed, f"test_{metric_name}_injected"], sdc_threshold)
                false_positive = metric_classification_functions[metric_name]["false_positive"](baseline, csv.loc[filter_flag_seed, f"test_{metric_name}_injected"], sdc_threshold)
                precision = pandas.Series([true_positive[:i+1].sum() / (true_positive[:i+1].sum() + false_positive[:i+1].sum()) for i in range(len(true_positive))])
                print(experiment_full_id_seed, metric_name, sdc_threshold, precision.tolist()[-1])
                csv.loc[filter_flag_seed, f"SDC_{metric_name}_{sdc_threshold}_precision_per_seed"] = precision.tolist()
                csv.loc[filter_flag_seed, f"SDC_{metric_name}_{sdc_threshold}_true_positive_per_seed"] = true_positive.tolist()
                csv.loc[filter_flag_seed, f"SDC_{metric_name}_{sdc_threshold}_false_positive_per_seed"] = false_positive.tolist()
csv.head()

EBINo_resnet18_gtsrb accuracy 0.05 0.3705208051268165
EBINo_resnet18_gtsrb_1600 accuracy 0.05 0.4055354993983153
EBINo_resnet18_gtsrb_1615 accuracy 0.05 0.30833333333333335
EBINo_resnet18_gtsrb_1614 accuracy 0.05 0.2783333333333333
EBINo_resnet18_gtsrb_1611 accuracy 0.05 0.2966666666666667
EBINo_resnet18_gtsrb_1610 accuracy 0.05 0.2916666666666667
EBINo_resnet18_gtsrb_1612 accuracy 0.05 0.30833333333333335
EBINo_resnet18_gtsrb_1613 accuracy 0.05 0.30333333333333334
RBRNo_resnet18_gtsrb accuracy 0.05 0.0831326461805221
RBRNo_resnet18_gtsrb_1600 accuracy 0.05 0.10219731603008406
RBRNo_resnet18_gtsrb_1615 accuracy 0.05 0.05
RBRNo_resnet18_gtsrb_1614 accuracy 0.05 0.041666666666666664
RBRNo_resnet18_gtsrb_1610 accuracy 0.05 0.05
RBRNo_resnet18_gtsrb_1611 accuracy 0.05 0.043333333333333335
RBRNo_resnet18_gtsrb_1613 accuracy 0.05 0.03666666666666667
RBRNo_resnet18_gtsrb_1612 accuracy 0.05 0.06166666666666667
RBINo_resnet18_gtsrb accuracy 0.05 0.0578383206788745
RBINo_resnet18_gtsrb_1600 accu

EBRNw_resnet18_cifar10_1612 accuracy 0.05 0.16166666666666665
GBRNw_resnet18_cifar10 accuracy 0.05 0.33496275605214154
GBRNw_resnet18_cifar10_1600 accuracy 0.05 0.33559431524547806
GBRNw_resnet18_cifar10_1614 accuracy 0.05 0.3233333333333333
GBRNw_resnet18_cifar10_1615 accuracy 0.05 0.3233333333333333
GBRNw_resnet18_cifar10_1611 accuracy 0.05 0.33
GBRNw_resnet18_cifar10_1610 accuracy 0.05 0.3333333333333333
GBRNw_resnet18_cifar10_1612 accuracy 0.05 0.3333333333333333
GBRNw_resnet18_cifar10_1613 accuracy 0.05 0.3566666666666667
GBINw_resnet18_cifar10 accuracy 0.05 0.4722174584119362
GBINw_resnet18_cifar10_1600 accuracy 0.05 0.5090548251054329
GBINw_resnet18_cifar10_1614 accuracy 0.05 0.3983333333333333
GBINw_resnet18_cifar10_1615 accuracy 0.05 0.4
GBINw_resnet18_cifar10_1610 accuracy 0.05 0.36333333333333334
GBINw_resnet18_cifar10_1611 accuracy 0.05 0.3933333333333333
GBINw_resnet18_cifar10_1612 accuracy 0.05 0.405
GBINw_resnet18_cifar10_1613 accuracy 0.05 0.37833333333333335
RBRNo_vgg1

LBINo_vgg11_gtsrb_1613 accuracy 0.05 0.175
EBRNo_vgg11_gtsrb accuracy 0.05 0.09915269515053182
EBRNo_vgg11_gtsrb_1615 accuracy 0.05 0.09774436090225563
EBRNo_vgg11_gtsrb_1614 accuracy 0.05 0.12638580931263857
EBRNo_vgg11_gtsrb_1610 accuracy 0.05 0.10514786418400876
EBRNo_vgg11_gtsrb_1611 accuracy 0.05 0.0707395498392283
EBRNo_vgg11_gtsrb_1612 accuracy 0.05 0.09433962264150944
EBRNo_vgg11_gtsrb_1613 accuracy 0.05 0.10175054704595186
LBRNo_vgg11_cifar10 accuracy 0.05 0.06
LBRNo_vgg11_cifar10_1615 accuracy 0.05 0.065
LBRNo_vgg11_cifar10_1614 accuracy 0.05 0.055
LBRNo_vgg11_cifar10_1611 accuracy 0.05 0.07
LBRNo_vgg11_cifar10_1610 accuracy 0.05 0.05
LBRNo_vgg11_cifar10_1612 accuracy 0.05 0.058333333333333334
LBRNo_vgg11_cifar10_1613 accuracy 0.05 0.06166666666666667
EBRNo_resnet18_cifar10 accuracy 0.05 0.2531994981179423
EBRNo_resnet18_cifar10_1614 accuracy 0.05 0.2515151515151515
EBRNo_resnet18_cifar10_1615 accuracy 0.05 0.24205748865355523
EBRNo_resnet18_cifar10_1610 accuracy 0.05 0.22105

LBINw_vgg11_gtsrb accuracy 0.05 0.04
LBINw_vgg11_gtsrb_1614 accuracy 0.05 0.045
LBINw_vgg11_gtsrb_1615 accuracy 0.05 0.025
LBINw_vgg11_gtsrb_1611 accuracy 0.05 0.045
LBINw_vgg11_gtsrb_1610 accuracy 0.05 0.041666666666666664
LBINw_vgg11_gtsrb_1613 accuracy 0.05 0.045
LBINw_vgg11_gtsrb_1612 accuracy 0.05 0.03833333333333333
LBRNw_vgg11_gtsrb accuracy 0.05 0.01638888888888889
LBRNw_vgg11_gtsrb_1615 accuracy 0.05 0.015
LBRNw_vgg11_gtsrb_1614 accuracy 0.05 0.008333333333333333
LBRNw_vgg11_gtsrb_1611 accuracy 0.05 0.013333333333333334
LBRNw_vgg11_gtsrb_1610 accuracy 0.05 0.02666666666666667
LBRNw_vgg11_gtsrb_1613 accuracy 0.05 0.015
LBRNw_vgg11_gtsrb_1612 accuracy 0.05 0.02
LBRNw_resnet18_cifar10 accuracy 0.05 0.03944444444444444
LBRNw_resnet18_cifar10_1615 accuracy 0.05 0.03
LBRNw_resnet18_cifar10_1614 accuracy 0.05 0.035
LBRNw_resnet18_cifar10_1610 accuracy 0.05 0.043333333333333335
LBRNw_resnet18_cifar10_1611 accuracy 0.05 0.04833333333333333
LBRNw_resnet18_cifar10_1613 accuracy 0.05 0.04

level_0  i  random_seed  random_threshold                        timestamp  \
0        0  0         1600               0.0  2023-01-04T00:02:00.000018+0000   
1        1  1         1600               0.0  2023-01-04T00:02:12.197240+0000   
2        2  2         1600               0.0  2023-01-04T00:02:25.163125+0000   
3        3  3         1600               0.0  2023-01-04T00:02:30.733914+0000   
4        4  4         1600               0.0  2023-01-04T00:02:39.142023+0000   

                                          target_csv injection_type  \
0  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
1  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
2  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
3  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   
4  /home/acolucci/Documents/PhD/Projects/FaultInj...     activation   

  extra_injection_info                       layer_name    index  ...  \
0                  NaN           adapter.backbone.conv1  30-7-17  ...   
1                  NaN   adapter.backbone.layer4.0.relu  195-1-0  ...   
2                  NaN   adapter.backbone.layer2.1.relu   68-3-3  ...   
3                  NaN  adapter.backbone.layer2.0.conv2    4-4-2  ...   
4                  NaN                     adapter.head        9  ...   

   random_neuron approximate_activation_gradient_value  config_file  \
0            NaN                                   NaN          NaN   
1            NaN                                   NaN          NaN   
2            NaN                                   NaN          NaN   
3            NaN                                   NaN          NaN   
4            NaN                                   NaN          NaN   

   checkpoint_file  SDC_accuracy_0.05_precision  \
0              NaN                     1.000000   
1              NaN                     0.500000   
2              NaN                     0.666667   
3              NaN                     0.750000   
4              NaN                     0.600000   

   SDC_accuracy_0.05_true_positive SDC_accuracy_0.05_false_positive  \
0                             True                            False   
1                            False                             True   
2                             True                            False   
3                             True                            False   
4                            False                             True   

  SDC_accuracy_0.05_precision_per_seed  \
0                             1.000000   
1                             0.500000   
2                             0.666667   
3                             0.750000   
4                             0.600000   

  SDC_accuracy_0.05_true_positive_per_seed  \
0                                     True   
1                                    False   
2                                     True   
3                                     True   
4                                    False   

  SDC_accuracy_0.05_false_positive_per_seed  
0                                     False  
1                                      True  
2                                     False  
3                                     False  
4                                      True  

[5 rows x 31 columns]

In [8]:
# for name, csv_dict in csv_list.copy().items():
#     csv = csv_dict["csv"]
    
#     # substitute inf and nan with max representable number
#     csv = csv.replace(float("NaN"), max_float)
#     csv = csv.replace(float("inf"), max_float)
#     csv = csv.replace(float("-inf"), -max_float)
    
#     csv_list[name]["csv"] = csv

In [9]:
# for name, csv_dict in csv_list.copy().items():
#     csv = csv_dict["csv"]
#     for metric_name in metric_names:
#         for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]): 
#             print(f"{name}, SDC_{metric_name}_{sdc_threshold}_precision: {csv[f'SDC_{metric_name}_{sdc_threshold}_precision'].tolist()[-1]}")

In [10]:
# conversion_dict = {"importance": "IBIN", "random": "RBRN", "importance-bit-random-neuron": "IBRN", "random-bit-importance-neuron": "RBIN"}
sdc_alltogether_histogram_csv_dict = {"experiment_full_id": [], "experiment": [], "configuration": [], "configuration_nice": [], "precision": [], "accuracy_delta": []}
for experiment_full_id in pandas.unique(csv["experiment_full_id"]):
    filter_flag = csv["experiment_full_id"] == experiment_full_id
    for metric_name in metric_names:
        for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]):
            print(experiment_full_id, metric_name, sdc_threshold)
            sdc_alltogether_histogram_csv_dict["experiment_full_id"].append(experiment_full_id)
            sdc_alltogether_histogram_csv_dict["experiment"].append(csv.loc[filter_flag, "experiment_code"].explode().tolist()[0])
            sdc_alltogether_histogram_csv_dict["configuration"].append(csv.loc[filter_flag, "experiment_config"].explode().tolist()[0])
            sdc_alltogether_histogram_csv_dict["configuration_nice"].append(configuration_name_to_nice_name_mapping[sdc_alltogether_histogram_csv_dict["configuration"][-1]])
            sdc_alltogether_histogram_csv_dict["precision"].append(csv.loc[filter_flag, f'SDC_{metric_name}_{sdc_threshold}_precision'].dropna().tolist()[-1])
            sdc_alltogether_histogram_csv_dict["accuracy_delta"].append(sdc_threshold)
sdc_alltogether_histogram_csv = pandas.DataFrame(sdc_alltogether_histogram_csv_dict)


sdc_alltogether_histogram_csv = sdc_alltogether_histogram_csv.sort_values(by="experiment", key=lambda x: [experiment_sorting_list.index(y) for y in x])

flag = None
for e in alltogether_experiments_to_plot:
    if flag is None:
        flag = sdc_alltogether_histogram_csv["experiment"] == e
    else:
        flag = flag | (sdc_alltogether_histogram_csv["experiment"] == e)
sdc_alltogether_histogram_csv = sdc_alltogether_histogram_csv[flag]


sdc_alltogether_histogram_csv.head()

EBINo_resnet18_gtsrb accuracy 0.05
RBRNo_resnet18_gtsrb accuracy 0.05
RBINo_resnet18_gtsrb accuracy 0.05
EBRNo_resnet18_gtsrb accuracy 0.05
GBINo_resnet18_gtsrb accuracy 0.05
GBRNo_resnet18_gtsrb accuracy 0.05
EBINw_resnet18_gtsrb accuracy 0.05
RBRNw_resnet18_gtsrb accuracy 0.05
RBINw_resnet18_gtsrb accuracy 0.05
EBRNw_resnet18_gtsrb accuracy 0.05
GBINw_resnet18_gtsrb accuracy 0.05
GBRNw_resnet18_gtsrb accuracy 0.05
RBRNo_resnet18_cifar10 accuracy 0.05
EBINo_resnet18_cifar10 accuracy 0.05
RBRNw_resnet18_cifar10 accuracy 0.05
RBINw_resnet18_cifar10 accuracy 0.05
EBINw_resnet18_cifar10 accuracy 0.05
EBRNw_resnet18_cifar10 accuracy 0.05
GBRNw_resnet18_cifar10 accuracy 0.05
GBINw_resnet18_cifar10 accuracy 0.05
RBRNo_vgg11_gtsrb accuracy 0.05
EBINo_vgg11_gtsrb accuracy 0.05
RBRNw_vgg11_gtsrb accuracy 0.05
RBINw_vgg11_gtsrb accuracy 0.05
EBINw_vgg11_gtsrb accuracy 0.05
EBRNw_vgg11_gtsrb accuracy 0.05
GBRNw_vgg11_gtsrb accuracy 0.05
GBINw_vgg11_gtsrb accuracy 0.05
RBRNo_vgg11_cifar10 accuracy

experiment_full_id experiment     configuration   configuration_nice  \
63     GBINo_vgg11_cifar10      GBINo     vgg11_cifar10     VGG11<br>CIFAR10   
50       GBINo_vgg11_gtsrb      GBINo       vgg11_gtsrb       VGG11<br>GTSRB   
47  GBINo_resnet18_cifar10      GBINo  resnet18_cifar10  ResNet18<br>CIFAR10   
4     GBINo_resnet18_gtsrb      GBINo    resnet18_gtsrb    ResNet18<br>GTSRB   
52  GBRNo_resnet18_cifar10      GBRNo  resnet18_cifar10  ResNet18<br>CIFAR10   

    precision  accuracy_delta  
63   0.593611            0.05  
50   0.472500            0.05  
47   0.571111            0.05  
4    0.582713            0.05  
52   0.516952            0.05

In [11]:
# conversion_dict = {"importance": "IBIN", "random": "RBRN", "importance-bit-random-neuron": "IBRN", "random-bit-importance-neuron": "RBIN"}
sdc_alltogether_histogram_avg_csv_dict = {"experiment_full_id_seed": [], "experiment_full_id": [], "experiment": [], "configuration": [], "configuration_nice": [], "precision": [], "accuracy_delta": []}
for experiment_full_id_seed in pandas.unique(csv["experiment_full_id_seed"]):
    filter_flag = csv["experiment_full_id_seed"] == experiment_full_id_seed
    for metric_name in metric_names:
        for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]):
            print(experiment_full_id_seed, metric_name, sdc_threshold)
            sdc_alltogether_histogram_avg_csv_dict["experiment_full_id_seed"].append(experiment_full_id_seed)
            sdc_alltogether_histogram_avg_csv_dict["experiment_full_id"].append(csv.loc[filter_flag, "experiment_full_id"].explode().tolist()[0])
            sdc_alltogether_histogram_avg_csv_dict["experiment"].append(csv.loc[filter_flag, "experiment_code"].explode().tolist()[0])
            sdc_alltogether_histogram_avg_csv_dict["configuration"].append(csv.loc[filter_flag, "experiment_config"].explode().tolist()[0])
            sdc_alltogether_histogram_avg_csv_dict["configuration_nice"].append(configuration_name_to_nice_name_mapping[sdc_alltogether_histogram_avg_csv_dict["configuration"][-1]])
            sdc_alltogether_histogram_avg_csv_dict["precision"].append(csv.loc[filter_flag, f'SDC_{metric_name}_{sdc_threshold}_precision_per_seed'].dropna().tolist()[-1])
            sdc_alltogether_histogram_avg_csv_dict["accuracy_delta"].append(sdc_threshold)
sdc_alltogether_histogram_avg_csv = pandas.DataFrame(sdc_alltogether_histogram_csv_dict)


sdc_alltogether_histogram_avg_csv = sdc_alltogether_histogram_avg_csv.sort_values(by="experiment", key=lambda x: [experiment_sorting_list.index(y) for y in x])

flag = None
for e in alltogether_experiments_to_plot:
    if flag is None:
        flag = sdc_alltogether_histogram_avg_csv["experiment"] == e
    else:
        flag = flag | (sdc_alltogether_histogram_avg_csv["experiment"] == e)
sdc_alltogether_histogram_csv = sdc_alltogether_histogram_avg_csv[flag]


sdc_alltogether_histogram_avg_csv.head()

EBINo_resnet18_gtsrb_1600 accuracy 0.05
RBRNo_resnet18_gtsrb_1600 accuracy 0.05
RBINo_resnet18_gtsrb_1600 accuracy 0.05
EBRNo_resnet18_gtsrb_1600 accuracy 0.05
GBINo_resnet18_gtsrb_1600 accuracy 0.05
GBINo_resnet18_gtsrb_1601 accuracy 0.05
GBRNo_resnet18_gtsrb_1600 accuracy 0.05
GBRNo_resnet18_gtsrb_1601 accuracy 0.05
EBINw_resnet18_gtsrb_1600 accuracy 0.05
RBRNw_resnet18_gtsrb_1600 accuracy 0.05
RBINw_resnet18_gtsrb_1600 accuracy 0.05
EBRNw_resnet18_gtsrb_1600 accuracy 0.05
GBINw_resnet18_gtsrb_1600 accuracy 0.05
GBRNw_resnet18_gtsrb_1600 accuracy 0.05
RBRNo_resnet18_cifar10_1600 accuracy 0.05
EBINo_resnet18_cifar10_1600 accuracy 0.05
RBRNw_resnet18_cifar10_1600 accuracy 0.05
RBINw_resnet18_cifar10_1600 accuracy 0.05
EBINw_resnet18_cifar10_1600 accuracy 0.05
EBRNw_resnet18_cifar10_1600 accuracy 0.05
GBRNw_resnet18_cifar10_1600 accuracy 0.05
GBINw_resnet18_cifar10_1600 accuracy 0.05
RBRNo_vgg11_gtsrb_1600 accuracy 0.05
EBINo_vgg11_gtsrb_1600 accuracy 0.05
RBRNw_vgg11_gtsrb_1600 accurac

GBRNw_resnet18_cifar10_1611 accuracy 0.05
LBRNo_vgg11_gtsrb_1611 accuracy 0.05
GBRNw_resnet18_gtsrb_1611 accuracy 0.05
LBINw_resnet18_gtsrb_1610 accuracy 0.05
EBINw_resnet18_gtsrb_1610 accuracy 0.05
EBRNo_resnet18_gtsrb_1611 accuracy 0.05
GBINw_vgg11_cifar10_1610 accuracy 0.05
EBINo_resnet18_cifar10_1611 accuracy 0.05
LBINo_resnet18_gtsrb_1611 accuracy 0.05
EBINw_resnet18_cifar10_1611 accuracy 0.05
EBINo_resnet18_gtsrb_1611 accuracy 0.05
RBINo_resnet18_gtsrb_1610 accuracy 0.05
EBINw_resnet18_gtsrb_1611 accuracy 0.05
RBINo_vgg11_cifar10_1610 accuracy 0.05
LBRNo_vgg11_gtsrb_1610 accuracy 0.05
LBINw_vgg11_gtsrb_1611 accuracy 0.05
RBRNw_resnet18_gtsrb_1611 accuracy 0.05
GBINw_vgg11_cifar10_1611 accuracy 0.05
LBINw_resnet18_cifar10_1610 accuracy 0.05
LBINo_vgg11_gtsrb_1611 accuracy 0.05
EBINo_vgg11_cifar10_1610 accuracy 0.05
RBRNw_vgg11_cifar10_1611 accuracy 0.05
RBINw_vgg11_cifar10_1610 accuracy 0.05
EBINw_vgg11_cifar10_1611 accuracy 0.05
RBINw_vgg11_gtsrb_1610 accuracy 0.05
LBRNo_resnet18

RBRNw_vgg11_gtsrb_1613 accuracy 0.05
RBINw_resnet18_cifar10_1613 accuracy 0.05
EBINo_vgg11_gtsrb_1612 accuracy 0.05
EBRNw_resnet18_gtsrb_1612 accuracy 0.05
EBINo_vgg11_cifar10_1613 accuracy 0.05
LBINw_vgg11_gtsrb_1612 accuracy 0.05


experiment_full_id experiment     configuration   configuration_nice  \
63     GBINo_vgg11_cifar10      GBINo     vgg11_cifar10     VGG11<br>CIFAR10   
50       GBINo_vgg11_gtsrb      GBINo       vgg11_gtsrb       VGG11<br>GTSRB   
47  GBINo_resnet18_cifar10      GBINo  resnet18_cifar10  ResNet18<br>CIFAR10   
4     GBINo_resnet18_gtsrb      GBINo    resnet18_gtsrb    ResNet18<br>GTSRB   
52  GBRNo_resnet18_cifar10      GBRNo  resnet18_cifar10  ResNet18<br>CIFAR10   

    precision  accuracy_delta  
63   0.593611            0.05  
50   0.472500            0.05  
47   0.571111            0.05  
4    0.582713            0.05  
52   0.516952            0.05

In [12]:
experiment_full_id_seed

'LBINw_vgg11_gtsrb_1612'

In [13]:
# conversion_dict = {"importance": "IBIN", "random": "RBRN", "importance-bit-random-neuron": "IBRN", "random-bit-importance-neuron": "RBIN"}
sdc_histogram_csv_dict = {"experiment_full_id": [], "experiment": [], "configuration": [], "configuration_nice": [], "precision": [], "accuracy_delta": []}
for experiment_full_id in histogram_experiment_full_ids_to_plot:
    filter_flag = csv["experiment_full_id"] == experiment_full_id
    for metric_name in metric_names:
        baseline = pandas.unique(csv.loc[filter_flag, f"test_{metric_name}_baseline"])[0]
        for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]):
            print(experiment_full_id, metric_name, sdc_threshold)
            sdc_histogram_csv_dict["experiment_full_id"].append(experiment_full_id)
            sdc_histogram_csv_dict["experiment"].append(csv.loc[filter_flag, "experiment_code"].explode().tolist()[0])
            sdc_histogram_csv_dict["configuration"].append(csv.loc[filter_flag, "experiment_config"].explode().tolist()[0])
            sdc_histogram_csv_dict["configuration_nice"].append(configuration_name_to_nice_name_mapping[sdc_alltogether_histogram_csv_dict["configuration"][-1]])
            sdc_histogram_csv_dict["precision"].append(csv.loc[filter_flag, f'SDC_{metric_name}_{sdc_threshold}_precision'].dropna().tolist()[-1])
            sdc_histogram_csv_dict["accuracy_delta"].append(sdc_threshold)
sdc_histogram_csv = pandas.DataFrame(sdc_histogram_csv_dict)
sdc_histogram_csv.head()

GBINw_resnet18_cifar10 accuracy 0.05
GBRNw_resnet18_cifar10 accuracy 0.05
EBINw_resnet18_cifar10 accuracy 0.05
EBRNw_resnet18_cifar10 accuracy 0.05
LBINw_resnet18_cifar10 accuracy 0.05
LBRNw_resnet18_cifar10 accuracy 0.05
RBINw_resnet18_cifar10 accuracy 0.05
RBRNw_resnet18_cifar10 accuracy 0.05


experiment_full_id experiment     configuration configuration_nice  \
0  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   
1  GBRNw_resnet18_cifar10      GBRNw  resnet18_cifar10   VGG11<br>CIFAR10   
2  EBINw_resnet18_cifar10      EBINw  resnet18_cifar10   VGG11<br>CIFAR10   
3  EBRNw_resnet18_cifar10      EBRNw  resnet18_cifar10   VGG11<br>CIFAR10   
4  LBINw_resnet18_cifar10      LBINw  resnet18_cifar10   VGG11<br>CIFAR10   

   precision  accuracy_delta  
0   0.472217            0.05  
1   0.334963            0.05  
2   0.247165            0.05  
3   0.174315            0.05  
4   0.050833            0.05

In [14]:
# conversion_dict = {"importance": "IBIN", "random": "RBRN", "importance-bit-random-neuron": "IBRN", "random-bit-importance-neuron": "RBIN"}
sdc_line_csv_dict = {"experiment_full_id": [], "experiment": [], "configuration": [], "configuration_nice": [], "precision": [], "accuracy_delta": [], "n_samples": []}
for experiment_full_id in line_experiment_full_ids_to_plot:
    filter_flag = csv["experiment_full_id"] == experiment_full_id
    for metric_name in metric_names:
        baseline = pandas.unique(csv.loc[filter_flag, f"test_{metric_name}_baseline"])[0]
        for i, sdc_threshold in enumerate(sdc_thresholds[metric_name]):
            for j, precision in enumerate(csv.loc[filter_flag, f'SDC_{metric_name}_{sdc_threshold}_precision'], start=1):
                print(experiment_full_id, metric_name, sdc_threshold, j, precision)
                sdc_line_csv_dict["experiment_full_id"].append(experiment_full_id)
                sdc_line_csv_dict["experiment"].append(csv.loc[filter_flag, "experiment_code"].explode().tolist()[0])
                sdc_line_csv_dict["configuration"].append(csv.loc[filter_flag, "experiment_config"].explode().tolist()[0])
                sdc_line_csv_dict["configuration_nice"].append(configuration_name_to_nice_name_mapping[sdc_alltogether_histogram_csv_dict["configuration"][-1]])
                sdc_line_csv_dict["precision"].append(precision)
                sdc_line_csv_dict["accuracy_delta"].append(sdc_threshold)
                sdc_line_csv_dict["n_samples"].append(j)
sdc_line_csv = pandas.DataFrame(sdc_line_csv_dict)
sdc_line_csv.head()

GBINw_resnet18_cifar10 accuracy 0.05 1 0.0
GBINw_resnet18_cifar10 accuracy 0.05 2 0.5
GBINw_resnet18_cifar10 accuracy 0.05 3 0.3333333333333333
GBINw_resnet18_cifar10 accuracy 0.05 4 0.25
GBINw_resnet18_cifar10 accuracy 0.05 5 0.4
GBINw_resnet18_cifar10 accuracy 0.05 6 0.3333333333333333
GBINw_resnet18_cifar10 accuracy 0.05 7 0.2857142857142857
GBINw_resnet18_cifar10 accuracy 0.05 8 0.375
GBINw_resnet18_cifar10 accuracy 0.05 9 0.4444444444444444
GBINw_resnet18_cifar10 accuracy 0.05 10 0.4
GBINw_resnet18_cifar10 accuracy 0.05 11 0.45454545454545453
GBINw_resnet18_cifar10 accuracy 0.05 12 0.4166666666666667
GBINw_resnet18_cifar10 accuracy 0.05 13 0.46153846153846156
GBINw_resnet18_cifar10 accuracy 0.05 14 0.5
GBINw_resnet18_cifar10 accuracy 0.05 15 0.4666666666666667
GBINw_resnet18_cifar10 accuracy 0.05 16 0.4375
GBINw_resnet18_cifar10 accuracy 0.05 17 0.47058823529411764
GBINw_resnet18_cifar10 accuracy 0.05 18 0.5
GBINw_resnet18_cifar10 accuracy 0.05 19 0.5263157894736842
GBINw_resnet18

GBINw_resnet18_cifar10 accuracy 0.05 155 0.5032258064516129
GBINw_resnet18_cifar10 accuracy 0.05 156 0.5
GBINw_resnet18_cifar10 accuracy 0.05 157 0.4968152866242038
GBINw_resnet18_cifar10 accuracy 0.05 158 0.4936708860759494
GBINw_resnet18_cifar10 accuracy 0.05 159 0.4968553459119497
GBINw_resnet18_cifar10 accuracy 0.05 160 0.49375
GBINw_resnet18_cifar10 accuracy 0.05 161 0.4906832298136646
GBINw_resnet18_cifar10 accuracy 0.05 162 0.4876543209876543
GBINw_resnet18_cifar10 accuracy 0.05 163 0.48466257668711654
GBINw_resnet18_cifar10 accuracy 0.05 164 0.4878048780487805
GBINw_resnet18_cifar10 accuracy 0.05 165 0.4909090909090909
GBINw_resnet18_cifar10 accuracy 0.05 166 0.4879518072289157
GBINw_resnet18_cifar10 accuracy 0.05 167 0.48502994011976047
GBINw_resnet18_cifar10 accuracy 0.05 168 0.4880952380952381
GBINw_resnet18_cifar10 accuracy 0.05 169 0.4911242603550296
GBINw_resnet18_cifar10 accuracy 0.05 170 0.48823529411764705
GBINw_resnet18_cifar10 accuracy 0.05 171 0.4853801169590643
GBI

GBINw_resnet18_cifar10 accuracy 0.05 309 0.511326860841424
GBINw_resnet18_cifar10 accuracy 0.05 310 0.5096774193548387
GBINw_resnet18_cifar10 accuracy 0.05 311 0.5112540192926045
GBINw_resnet18_cifar10 accuracy 0.05 312 0.5096153846153846
GBINw_resnet18_cifar10 accuracy 0.05 313 0.5079872204472844
GBINw_resnet18_cifar10 accuracy 0.05 314 0.5063694267515924
GBINw_resnet18_cifar10 accuracy 0.05 315 0.5047619047619047
GBINw_resnet18_cifar10 accuracy 0.05 316 0.5063291139240507
GBINw_resnet18_cifar10 accuracy 0.05 317 0.5047318611987381
GBINw_resnet18_cifar10 accuracy 0.05 318 0.5062893081761006
GBINw_resnet18_cifar10 accuracy 0.05 319 0.5078369905956113
GBINw_resnet18_cifar10 accuracy 0.05 320 0.509375
GBINw_resnet18_cifar10 accuracy 0.05 321 0.5077881619937694
GBINw_resnet18_cifar10 accuracy 0.05 322 0.5062111801242236
GBINw_resnet18_cifar10 accuracy 0.05 323 0.5077399380804953
GBINw_resnet18_cifar10 accuracy 0.05 324 0.5092592592592593
GBINw_resnet18_cifar10 accuracy 0.05 325 0.51076923

GBINw_resnet18_cifar10 accuracy 0.05 462 0.5108225108225108
GBINw_resnet18_cifar10 accuracy 0.05 463 0.5118790496760259
GBINw_resnet18_cifar10 accuracy 0.05 464 0.5107758620689655
GBINw_resnet18_cifar10 accuracy 0.05 465 0.5118279569892473
GBINw_resnet18_cifar10 accuracy 0.05 466 0.5128755364806867
GBINw_resnet18_cifar10 accuracy 0.05 467 0.5117773019271948
GBINw_resnet18_cifar10 accuracy 0.05 468 0.5128205128205128
GBINw_resnet18_cifar10 accuracy 0.05 469 0.511727078891258
GBINw_resnet18_cifar10 accuracy 0.05 470 0.5106382978723404
GBINw_resnet18_cifar10 accuracy 0.05 471 0.5116772823779193
GBINw_resnet18_cifar10 accuracy 0.05 472 0.510593220338983
GBINw_resnet18_cifar10 accuracy 0.05 473 0.5116279069767442
GBINw_resnet18_cifar10 accuracy 0.05 474 0.510548523206751
GBINw_resnet18_cifar10 accuracy 0.05 475 0.511578947368421
GBINw_resnet18_cifar10 accuracy 0.05 476 0.5105042016806722
GBINw_resnet18_cifar10 accuracy 0.05 477 0.5094339622641509
GBINw_resnet18_cifar10 accuracy 0.05 478 0.5

GBINw_resnet18_cifar10 accuracy 0.05 614 0.50814332247557
GBINw_resnet18_cifar10 accuracy 0.05 615 0.5089430894308943
GBINw_resnet18_cifar10 accuracy 0.05 616 0.5081168831168831
GBINw_resnet18_cifar10 accuracy 0.05 617 0.5072933549432739
GBINw_resnet18_cifar10 accuracy 0.05 618 0.5080906148867314
GBINw_resnet18_cifar10 accuracy 0.05 619 0.5088852988691438
GBINw_resnet18_cifar10 accuracy 0.05 620 0.5080645161290323
GBINw_resnet18_cifar10 accuracy 0.05 621 0.5088566827697263
GBINw_resnet18_cifar10 accuracy 0.05 622 0.5080385852090032
GBINw_resnet18_cifar10 accuracy 0.05 623 0.5088282504012841
GBINw_resnet18_cifar10 accuracy 0.05 624 0.5080128205128205
GBINw_resnet18_cifar10 accuracy 0.05 625 0.5072
GBINw_resnet18_cifar10 accuracy 0.05 626 0.5063897763578274
GBINw_resnet18_cifar10 accuracy 0.05 627 0.5055821371610846
GBINw_resnet18_cifar10 accuracy 0.05 628 0.5047770700636943
GBINw_resnet18_cifar10 accuracy 0.05 629 0.5039745627980922
GBINw_resnet18_cifar10 accuracy 0.05 630 0.50317460317

...

RBRNw_resnet18_cifar10 accuracy 0.05 12746 0.038521889220147494
RBRNw_resnet18_cifar10 accuracy 0.05 12747 0.038518867184435555
RBRNw_resnet18_cifar10 accuracy 0.05 12748 0.0385158456228428
RBRNw_resnet18_cifar10 accuracy 0.05 12749 0.038512824535257666
RBRNw_resnet18_cifar10 accuracy 0.05 12750 0.03850980392156863
RBRNw_resnet18_cifar10 accuracy 0.05 12751 0.03850678378166418
RBRNw_resnet18_cifar10 accuracy 0.05 12752 0.038503764115432874
RBRNw_resnet18_cifar10 accuracy 0.05 12753 0.03850074492276327
RBRNw_resnet18_cifar10 accuracy 0.05 12754 0.03849772620354398
RBRNw_resnet18_cifar10 accuracy 0.05 12755 0.038573108584868676
RBRNw_resnet18_cifar10 accuracy 0.05 12756 0.03857008466603951
RBRNw_resnet18_cifar10 accuracy 0.05 12757 0.03856706122129027
RBRNw_resnet18_cifar10 accuracy 0.05 12758 0.03864242044207556
RBRNw_resnet18_cifar10 accuracy 0.05 12759 0.03863939180186535
RBRNw_resnet18_cifar10 accuracy 0.05 12760 0.038636363636363635
RBRNw_resnet18_cifar10 accuracy 0.05 12761 0.03863

RBRNw_resnet18_cifar10 accuracy 0.05 12883 0.03842272762555306
RBRNw_resnet18_cifar10 accuracy 0.05 12884 0.03841974542067681
RBRNw_resnet18_cifar10 accuracy 0.05 12885 0.03841676367869616
RBRNw_resnet18_cifar10 accuracy 0.05 12886 0.038413782399503334
RBRNw_resnet18_cifar10 accuracy 0.05 12887 0.03841080158299061
RBRNw_resnet18_cifar10 accuracy 0.05 12888 0.03840782122905028
RBRNw_resnet18_cifar10 accuracy 0.05 12889 0.03840484133757468
RBRNw_resnet18_cifar10 accuracy 0.05 12890 0.03840186190845617
RBRNw_resnet18_cifar10 accuracy 0.05 12891 0.03839888294158715
RBRNw_resnet18_cifar10 accuracy 0.05 12892 0.03839590443686007
RBRNw_resnet18_cifar10 accuracy 0.05 12893 0.03839292639416738
RBRNw_resnet18_cifar10 accuracy 0.05 12894 0.03838994881340158
RBRNw_resnet18_cifar10 accuracy 0.05 12895 0.038386971694455214
RBRNw_resnet18_cifar10 accuracy 0.05 12896 0.03838399503722084
RBRNw_resnet18_cifar10 accuracy 0.05 12897 0.03838101884159107
RBRNw_resnet18_cifar10 accuracy 0.05 12898 0.03837804

RBRNw_resnet18_cifar10 accuracy 0.05 13020 0.038018433179723504
RBRNw_resnet18_cifar10 accuracy 0.05 13021 0.03801551340142846
RBRNw_resnet18_cifar10 accuracy 0.05 13022 0.03801259407157119
RBRNw_resnet18_cifar10 accuracy 0.05 13023 0.03800967519004837
RBRNw_resnet18_cifar10 accuracy 0.05 13024 0.03800675675675676
RBRNw_resnet18_cifar10 accuracy 0.05 13025 0.03800383877159309
RBRNw_resnet18_cifar10 accuracy 0.05 13026 0.03800092123445417
RBRNw_resnet18_cifar10 accuracy 0.05 13027 0.03799800414523682
RBRNw_resnet18_cifar10 accuracy 0.05 13028 0.037995087503837885
RBRNw_resnet18_cifar10 accuracy 0.05 13029 0.03799217131015427
RBRNw_resnet18_cifar10 accuracy 0.05 13030 0.037989255564082884
RBRNw_resnet18_cifar10 accuracy 0.05 13031 0.03798634026552068
RBRNw_resnet18_cifar10 accuracy 0.05 13032 0.03798342541436464
RBRNw_resnet18_cifar10 accuracy 0.05 13033 0.03798051101051178
RBRNw_resnet18_cifar10 accuracy 0.05 13034 0.037977597053859134
RBRNw_resnet18_cifar10 accuracy 0.05 13035 0.037974

RBRNw_resnet18_cifar10 accuracy 0.05 13159 0.03799680826810548
RBRNw_resnet18_cifar10 accuracy 0.05 13160 0.037993920972644375
RBRNw_resnet18_cifar10 accuracy 0.05 13161 0.03799103411594864
RBRNw_resnet18_cifar10 accuracy 0.05 13162 0.03798814769791825
RBRNw_resnet18_cifar10 accuracy 0.05 13163 0.03798526171845324
RBRNw_resnet18_cifar10 accuracy 0.05 13164 0.03798237617745366
RBRNw_resnet18_cifar10 accuracy 0.05 13165 0.0379794910748196
RBRNw_resnet18_cifar10 accuracy 0.05 13166 0.03797660641045116
RBRNw_resnet18_cifar10 accuracy 0.05 13167 0.0379737221842485
RBRNw_resnet18_cifar10 accuracy 0.05 13168 0.03797083839611179
RBRNw_resnet18_cifar10 accuracy 0.05 13169 0.03796795504594123
RBRNw_resnet18_cifar10 accuracy 0.05 13170 0.037965072133637055
RBRNw_resnet18_cifar10 accuracy 0.05 13171 0.03796218965909954
RBRNw_resnet18_cifar10 accuracy 0.05 13172 0.03795930762222897
RBRNw_resnet18_cifar10 accuracy 0.05 13173 0.037956426022925684
RBRNw_resnet18_cifar10 accuracy 0.05 13174 0.037953544

experiment_full_id experiment     configuration configuration_nice  \
0  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   
1  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   
2  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   
3  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   
4  GBINw_resnet18_cifar10      GBINw  resnet18_cifar10   VGG11<br>CIFAR10   

   precision  accuracy_delta  n_samples  
0   0.000000            0.05          1  
1   0.500000            0.05          2  
2   0.333333            0.05          3  
3   0.250000            0.05          4  
4   0.400000            0.05          5

# Plotting

In [15]:
# df = plotly.express.data.tips()
# fig = plotly.express.bar(df, x="day", y="total_bill", color="smoker", barmode="group", facet_col="sex",
#              category_orders={"day": ["Thur", "Fri", "Sat", "Sun"],
#                               "smoker": ["Yes", "No"],
#                               "sex": ["Male", "Female"]})
# fig.show()
alltogether_colors = plotly.colors.sample_colorscale(plotly.express.colors.cmocean.balance, len(pandas.unique(sdc_alltogether_histogram_csv["experiment"])))
fig_alltogether = plotly.express.histogram(
    sdc_alltogether_histogram_csv,
    x="configuration_nice",
    y="precision",
    color="experiment",
    barmode="group",
    histfunc="avg",
    labels=dict(precision="Precision", experiment=""),
    text_auto=".3f",
    # pattern_shape="experiment",
    # color_discrete_sequence=plotly.express.colors.colorbrewer.PuOr[::2],
    color_discrete_sequence=alltogether_colors,
    category_orders={
#         "experiment": [x.split("_")[0] for x in histogram_experiment_full_ids_to_plot],
        "configuration_nice": configuration_order,
    }
)
fig_alltogether.update_layout(
    barmode="group",
    xaxis={"title": ''},
    yaxis={"title": "Precision"},
    
    font={'size': 24},
    template="presentation",
    margin=dict(l=70, t=20, b=70, r=0),
    legend=dict(
#         x=0.1,  # value must be between 0 to 1.
#         y=1,   # value must be between 0 to 1.
        bordercolor="Black",
        borderwidth=1,
        font=dict(
            size=17,
        ),
        orientation="h",
    ),
#     annotations=[
#          dict(
#              text="G",
#              x=0.40,
#              ax=0.35,
#              y=0.15,
#              ay=0.4,
#              xref="x domain",
#              axref="x domain",
#              yref="y domain",
#              ayref="y domain",
# #              bgcolor="rgba(255, 255, 255, 0)",
# #              bordercolor="rgba(255, 255, 255, 0)",
#              bgcolor="green",
#              bordercolor='green',
#              borderwidth=3,
#              borderpad=0,
#              font=dict(
#                  color="white",
#                  size=50,
#              ),
#              arrowhead=2,
#              arrowsize=1.2,
#              arrowwidth=3,
#              arrowcolor="Green",
#          ),
#     ],
#     shapes=[
#         dict(
#             type="rect",
#             xref="x domain",
#             yref="y domain",
#             x0=0.31,
#             x1=0.5,
#             y0=0.03,
#             y1=0.15,
#             line=dict(
#                 color="Green",
#                 width=3,
#             ),
#         ),
# #         dict(
# #             type="circle",
# #             xref="x domain",
# #             yref="y domain",
# #             x0=0.4,
# #             x1=0.5,
# #             y0=0.15,
# #             y1=0.25,
# #             fillcolor="green",
# #             line=dict(
# #                 color="Green",
# #                 width=1,
# #             ),
# #         ),
#     ],
#     annotationdefaults=dict(
        
#     ),
)
# fig.write_html(base_ijcnn2023_result_path / "plots/histogram_plot_sdc.html")
fig_alltogether.show()

In [16]:
# df = plotly.express.data.tips()
# fig = plotly.express.bar(df, x="day", y="total_bill", color="smoker", barmode="group", facet_col="sex",
#              category_orders={"day": ["Thur", "Fri", "Sat", "Sun"],
#                               "smoker": ["Yes", "No"],
#                               "sex": ["Male", "Female"]})
# fig.show()

alltogether_avg_groupby_csv = sdc_alltogether_histogram_avg_csv.groupby(by=["experiment", "configuration_nice"])
alltogether_avg_csv_dict = {"configuration_nice": [], "precision": [], "experiment": [], "precision_std": []}
for (e, c), p, std in zip(alltogether_avg_groupby_csv.mean().index.tolist(), alltogether_avg_groupby_csv.mean()["precision"].tolist(), alltogether_avg_groupby_csv.std()["precision"].tolist()):
    alltogether_avg_csv_dict["configuration_nice"].append(c)
    alltogether_avg_csv_dict["precision"].append(p)
    alltogether_avg_csv_dict["experiment"].append(e)
    alltogether_avg_csv_dict["precision_std"].append(std)
alltogether_avg_csv = pandas.DataFrame(alltogether_avg_csv_dict)

alltogether_avg_colors = plotly.colors.sample_colorscale(plotly.express.colors.cmocean.haline, len(pandas.unique(alltogether_avg_csv["experiment"])))
fig_alltogether_avg = plotly.express.bar(
    alltogether_avg_csv,
    error_y="precision_std",
    x="configuration_nice",
    y="precision",
    color="experiment",
    barmode="group",
#     histfunc="avg",
    labels=dict(precision="Precision", experiment=""),
    text_auto=".3f",
    # pattern_shape="experiment",
    # color_discrete_sequence=plotly.express.colors.colorbrewer.PuOr[::2],
    color_discrete_sequence=alltogether_avg_colors,
)
fig_alltogether_avg.update_layout(
    barmode="group",
    xaxis={"title": ''},
    yaxis={"title": "Precision"},
    
    font={'size': 24},
    template="presentation",
    margin=dict(l=70, t=20, b=70, r=0),
    legend=dict(
#         x=0.1,  # value must be between 0 to 1.
#         y=1,   # value must be between 0 to 1.
        bordercolor="Black",
        borderwidth=1,
        font=dict(
            size=17,
        ),
        orientation="h",
    ),
)
# fig.write_html(base_ijcnn2023_result_path / "plots/histogram_plot_sdc.html")
fig_alltogether_avg.show()

In [17]:
# df = plotly.express.data.tips()
# fig = plotly.express.bar(df, x="day", y="total_bill", color="smoker", barmode="group", facet_col="sex",
#              category_orders={"day": ["Thur", "Fri", "Sat", "Sun"],
#                               "smoker": ["Yes", "No"],
#                               "sex": ["Male", "Female"]})
# fig.show()
histogram_colors = plotly.colors.sample_colorscale(plotly.express.colors.cmocean.haline, len(pandas.unique(sdc_histogram_csv["accuracy_delta"])))
fig_histogram = plotly.express.histogram(
    sdc_histogram_csv,
    x="experiment",
    y="precision",
    color="accuracy_delta",
    barmode="group",
    labels=dict(precision="Precision", accuracy_delta="SDC Threshold"),
    text_auto=".3f",
    # pattern_shape="accuracy_delta",
    # color_discrete_sequence=plotly.express.colors.colorbrewer.PuOr[::2],
    color_discrete_sequence=histogram_colors,
    category_orders={
#         "experiment": [x.split("_")[0] for x in histogram_experiment_full_ids_to_plot],
        "experiment": experiment_sorting_list,
    }
)
fig_histogram.update_layout(
    barmode="group",
    xaxis={"title": ''},
    yaxis={"title": "Precision",},
    
    font={'size': 24},
    template="presentation",
    margin=dict(l=90, t=20, b=30, r=0),
    legend=dict(
        x=0.5,  # value must be between 0 to 1.
        y=1,   # value must be between 0 to 1.
        bordercolor="Black",
        borderwidth=1,
    ),
#     annotations=[
#          dict(
#              text="G",
#              x=0.40,
#              ax=0.35,
#              y=0.15,
#              ay=0.4,
#              xref="x domain",
#              axref="x domain",
#              yref="y domain",
#              ayref="y domain",
# #              bgcolor="rgba(255, 255, 255, 0)",
# #              bordercolor="rgba(255, 255, 255, 0)",
#              bgcolor="green",
#              bordercolor='green',
#              borderwidth=3,
#              borderpad=0,
#              font=dict(
#                  color="white",
#                  size=50,
#              ),
#              arrowhead=2,
#              arrowsize=1.2,
#              arrowwidth=3,
#              arrowcolor="Green",
#          ),
#     ],
#     shapes=[
#         dict(
#             type="rect",
#             xref="x domain",
#             yref="y domain",
#             x0=0.31,
#             x1=0.5,
#             y0=0.03,
#             y1=0.15,
#             line=dict(
#                 color="Green",
#                 width=3,
#             ),
#         ),
# #         dict(
# #             type="circle",
# #             xref="x domain",
# #             yref="y domain",
# #             x0=0.4,
# #             x1=0.5,
# #             y0=0.15,
# #             y1=0.25,
# #             fillcolor="green",
# #             line=dict(
# #                 color="Green",
# #                 width=1,
# #             ),
# #         ),
#     ],
#     annotationdefaults=dict(
        
#     ),
)
# fig.write_html(base_ijcnn2023_result_path / "plots/histogram_plot_sdc.html")
fig_histogram.show()

ZeroDivisionError: division by zero

In [ ]:
fig = plotly.express.line(
    sdc_line_csv,
    x="n_samples",
    y="precision",
    color="experiment",
    # line_group="accuracy_delta",
    animation_frame="accuracy_delta",
)
# fig.write_html(base_ijcnn2023_result_path / "plots/line_plot_sdc.html")
fig.show()

In [ ]:
line_colors = plotly.colors.sample_colorscale(plotly.express.colors.cmocean.haline, len(pandas.unique(sdc_line_csv["experiment"])))
fig_line = plotly.express.line(
    sdc_line_csv.groupby(["experiment", "n_samples"], as_index=False).mean(),
    x="n_samples",
    y="precision",
    color="experiment",
    # line_group="accuracy_delta",
    # animation_frame="accuracy_delta",
    labels=dict(precision="Precision", n_samples="# Injections", experiment=""),
    # line_dash="experiment",
    # color_discrete_sequence=plotly.express.colors.colorbrewer.PuOr[::2],
    color_discrete_sequence=line_colors,
)
fig_line.update_layout(
    xaxis={"range": [0, 550]},
    yaxis={"range": [0, 0.65]},
    font={'size': 24},
    template="presentation",
    margin=dict(l=70, t=0, b=60, r=0),
    legend=dict(
        font=dict(size=18),
        x=0.15,  # value must be between 0 to 1.
        y=1,   # value must be between 0 to 1.
        bordercolor="Black",
        borderwidth=1,
        orientation="h",
#         tracegroupgap=1,
    ),
#     annotations=[
#          dict(
#              text="G",
#              x=0.40,
#              ax=0.35,
#              y=0.15,
#              ay=0.4,
#              xref="x domain",
#              axref="x domain",
#              yref="y domain",
#              ayref="y domain",
# #              bgcolor="rgba(255, 255, 255, 0)",
# #              bordercolor="rgba(255, 255, 255, 0)",
#              bgcolor="green",
#              bordercolor='green',
#              borderwidth=3,
#              borderpad=0,
#              font=dict(
#                  color="white",
#                  size=50,
#              ),
#              arrowhead=2,
#              arrowsize=1.2,
#              arrowwidth=3,
#              arrowcolor="Green",
#          ),
#     ],
#     shapes=[
#         dict(
#             type="rect",
#             xref="x domain",
#             yref="y domain",
#             x0=0.31,
#             x1=0.5,
#             y0=0.03,
#             y1=0.15,
#             line=dict(
#                 color="Green",
#                 width=3,
#             ),
#         ),
# #         dict(
# #             type="circle",
# #             xref="x domain",
# #             yref="y domain",
# #             x0=0.4,
# #             x1=0.5,
# #             y0=0.15,
# #             y1=0.25,
# #             fillcolor="green",
# #             line=dict(
# #                 color="Green",
# #                 width=1,
# #             ),
# #         ),
#     ],
#     annotationdefaults=dict(
        
#     ),
)
# fig.write_html(base_ijcnn2023_result_path / "plots/line_plot_sdc.html")
fig_line.show()

In [19]:
current_time = time.strftime(TIME_FORMAT)
for ____ in range(2):
    fig_alltogether.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__alltogether_histogram.pdf", format='pdf', height=360, width=1000)
    fig_alltogether.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__alltogether_histogram.svg", format='svg', height=360, width=1000)
#     fig_alltogether_avg.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__alltogether_avg_histogram.pdf", format='pdf', height=360, width=1000)
#     fig_alltogether_avg.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__alltogether_avg_histogram.svg", format='svg', height=360, width=1000)
    fig_line.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__line_plot_{histogram_line_injection_target}.pdf", format='pdf', height=360, width=1000)
    fig_line.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__line_plot_{histogram_line_injection_target}.svg", format='svg', height=360, width=1000)
    fig_histogram.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__histogram_plot_{histogram_line_injection_target}.pdf", format='pdf', height=360, width=800)
    fig_histogram.write_image(file=base_ijcnn2023_result_path / f"plots/{current_time}__histogram_plot_{histogram_line_injection_target}.svg", format='svg', height=360, width=800)
    time.sleep(2)